# 3+1 slicing of Kerr spacetime

This notebook demonstrates a few capabilities of SageMath in computations regarding the 3+1 slicing of Kerr spacetime. The corresponding tools have been developed within the  [SageManifolds](https://sagemanifolds.obspm.fr) project (version 1.3, as included in SageMath 8.3).

Click [here](https://raw.githubusercontent.com/sagemanifolds/SageManifolds/master/Worksheets/v1.3/SM_Kerr_3p1.ipynb) to download the notebook file (ipynb format). To run it, you must start SageMath within the Jupyter notebook, via the command `sage -n jupyter`

*NB:* a version of SageMath at least equal to 8.2 is required to run this notebook:

In [1]:
version()

'SageMath version 8.3, Release Date: 2018-08-03'

First we set up the notebook to display mathematical objects using LaTeX rendering:

In [2]:
%display latex

Since some computations are quite long, we ask for running them in parallel on 8 cores:

In [3]:
Parallelism().set(nproc=8)

## Spacelike hypersurface

We consider some hypersurface $\Sigma$ of a spacelike foliation $(\Sigma_t)_{t\in\mathbb{R}}$ of Kerr spacetime; we declare $\Sigma_t$ as a 3-dimensional Riemannian manifold:

In [4]:
Sig = Manifold(3, 'Sigma', latex_name=r'\Sigma', 
               structure='Riemannian', metric_name='gam', 
               metric_latex_name=r'\gamma', start_index=1)
print(Sig)

3-dimensional Riemannian manifold Sigma


On $\Sigma$, we consider the *"rational-polynomial" coordinates* $(r,y,\phi)$ inheritated from the standard Boyer-Lindquist coordinates $(t,r,\theta,\phi)$ of Kerr spacetime, via $y=\cos\theta$:

In [5]:
X.<r,y,ph> = Sig.chart(r'r:(1,+oo) y:(-1,1) ph:(0,2*pi):\phi')
print(X) ; X

Chart (Sigma, (r, y, ph))


Chart (Sigma, (r, y, ph))

<h3>Riemannian metric on $\Sigma$</h3>

<p>First the two Kerr parameters:</p>

In [6]:
var('m, a', domain='real')
assume(m > 0)
assume(a > 0)
assume(a^2-2*m*r+r^2 > 0)  # region where Sigma is spacelike
assumptions()

[r is real,
 r > 1,
 y is real,
 y > -1,
 y < 1,
 ph is real,
 ph > 0,
 ph < 2*pi,
 m is real,
 a is real,
 m > 0,
 a > 0,
 a^2 - 2*m*r + r^2 > 0]

<p>For dealing with extreme Kerr, the following must be uncommented:</p>

In [7]:
# m = 1 ; a = 1

<p>Some shortcut notations:</p>

In [8]:
rho2 = r^2 + a^2*y^2 
Del = r^2 -2*m*r + a^2
AA2 = rho2*(r^2 + a^2) + 2*a^2*m*r*(1-y^2)
BB2 = r^2 + a^2 + 2*a^2*m*r*(1-y^2)/rho2

The metric $\gamma$ induced by the spacetime metric $g$ on $\Sigma$:

In [9]:
gam = Sig.metric()
gam[1,1] = rho2/Del
gam[2,2] = rho2/(1-y^2)
gam[3,3] = BB2*(1-y^2)
gam.display()

gam = (a^2*y^2 + r^2)/(a^2 - 2*m*r + r^2) dr*dr - (a^2*y^2 + r^2)/(y^2 - 1) dy*dy + (2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) - a^2 - r^2)*(y^2 - 1) dph*dph

<p>A matrix view of the components w.r.t. coordinates $(r,y,\phi)$:</p>

In [10]:
gam[:]

[                        (a^2*y^2 + r^2)/(a^2 - 2*m*r + r^2)                                                           0                                                           0]
[                                                          0                                  -(a^2*y^2 + r^2)/(y^2 - 1)                                                           0]
[                                                          0                                                           0 (2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) - a^2 - r^2)*(y^2 - 1)]

<h3>Lapse function and shift vector</h3>

In [11]:
N = Sig.scalar_field(sqrt(Del / BB2), name='N')
print(N)
N.display()

Scalar field N on the 3-dimensional Riemannian manifold Sigma


N: Sigma --> R
   (r, y, ph) |--> sqrt(-(a^2 - 2*m*r + r^2)/(2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) - a^2 - r^2))

In [12]:
b = Sig.vector_field('beta', latex_name=r'\beta') 
b[3] = -2*m*r*a/AA2   
# unset components are zero 
b.display()

beta = 2*a*m*r/(2*(y^2 - 1)*a^2*m*r - (a^2*y^2 + r^2)*(a^2 + r^2)) d/dph

### Extrinsic curvature of $\Sigma$

We use the formula
$$ K_{ij} = \frac{1}{2N} \mathcal{L}_{\beta} \gamma_{ij} $$
which is valid for any stationary spacetime:

In [13]:
K = gam.lie_der(b) / (2*N)
K.set_name('K')
print(K) ; K.display()

Field of symmetric bilinear forms K on the 3-dimensional Riemannian manifold Sigma


K = (a^3*m*r^2 + 3*a*m*r^4 + (a^5*m - a^3*m*r^2)*y^4 - (a^5*m + 3*a*m*r^4)*y^2)*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)/((2*a^2*m*r^3 + a^2*r^4 + r^6 + (a^6 - 2*a^4*m*r + a^4*r^2)*y^4 + 2*(a^4*m*r + a^4*r^2 - a^2*m*r^3 + a^2*r^4)*y^2)*sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)) dr*dph - 2*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*((a^5*m*r - 2*a^3*m^2*r^2 + a^3*m*r^3)*y^3 - (a^5*m*r - 2*a^3*m^2*r^2 + a^3*m*r^3)*y)/((2*a^2*m*r^3 + a^2*r^4 + r^6 + (a^6 - 2*a^4*m*r + a^4*r^2)*y^4 + 2*(a^4*m*r + a^4*r^2 - a^2*m*r^3 + a^2*r^4)*y^2)*sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)) dy*dph + (a^3*m*r^2 + 3*a*m*r^4 + (a^5*m - a^3*m*r^2)*y^4 - (a^5*m + 3*a*m*r^4)*y^2)*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)/((2*a^2*m*r^3 + a^2*r^4 + r^6 + (a^6 - 2*a^4*m*r + a^4*r^2)*y^4 + 2*(a^4*m*r + a^4*r^2 - a^2*m*r^3 + a^2*r^4)*y^2)*sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)) dph*dr - 2*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*((a^5*m*r - 2*a^3*m^2*r^2 + a^3*m*r^3)*y^3 - (a^5*m*r - 2*a^3*m^2*r^2 + a^3*m*r^3)*y)/((2*a^2*m*r^3 + a^2*r^4 + r^6 + (a^6 - 2*a^4*m*r + a^4*r^2)*y^4 + 2*(a^4*m*r + a^4*r^2 - a^2*m*r^3 + a^2*r^4)*y^2)*sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)) dph*dy

<p>Check (comparison with known formulas):</p>

In [14]:
Krp = a*m*(1-y^2)*(3*r^4+a^2*r^2+a^2*(r^2-a^2)*y^2) / rho2^2/sqrt(Del*BB2)
Krp

((a^2 - r^2)*a^2*y^2 - a^2*r^2 - 3*r^4)*(y^2 - 1)*a*m/((a^2*y^2 + r^2)^2*sqrt(-(2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) - a^2 - r^2)*(a^2 - 2*m*r + r^2)))

In [15]:
K[1,3] - Krp

0

In [16]:
Kyp = 2*m*r*a^3*(1-y^2)*y*sqrt(Del)/rho2^2/sqrt(BB2)
Kyp

-2*sqrt(a^2 - 2*m*r + r^2)*(y^2 - 1)*a^3*m*r*y/(sqrt(-2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) + a^2 + r^2)*(a^2*y^2 + r^2)^2)

In [17]:
K[2,3] - Kyp

0

<p>For now on, we use the expressions Krp and Kyp above for $K_{r\phi}$ and $K_{ry}$, respectively:</p>

In [18]:
K1 = Sig.sym_bilin_form_field('K')
K1[1,3] = Krp
K1[2,3] = Kyp
K = K1
K.display()

K = ((a^2 - r^2)*a^2*y^2 - a^2*r^2 - 3*r^4)*(y^2 - 1)*a*m/((a^2*y^2 + r^2)^2*sqrt(-(2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) - a^2 - r^2)*(a^2 - 2*m*r + r^2))) dr*dph - 2*sqrt(a^2 - 2*m*r + r^2)*(y^2 - 1)*a^3*m*r*y/(sqrt(-2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) + a^2 + r^2)*(a^2*y^2 + r^2)^2) dy*dph + ((a^2 - r^2)*a^2*y^2 - a^2*r^2 - 3*r^4)*(y^2 - 1)*a*m/((a^2*y^2 + r^2)^2*sqrt(-(2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) - a^2 - r^2)*(a^2 - 2*m*r + r^2))) dph*dr - 2*sqrt(a^2 - 2*m*r + r^2)*(y^2 - 1)*a^3*m*r*y/(sqrt(-2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) + a^2 + r^2)*(a^2*y^2 + r^2)^2) dph*dy

In [19]:
K.display_comp()

K_r,ph = ((a^2 - r^2)*a^2*y^2 - a^2*r^2 - 3*r^4)*(y^2 - 1)*a*m/((a^2*y^2 + r^2)^2*sqrt(-(2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) - a^2 - r^2)*(a^2 - 2*m*r + r^2))) 
K_y,ph = -2*sqrt(a^2 - 2*m*r + r^2)*(y^2 - 1)*a^3*m*r*y/(sqrt(-2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) + a^2 + r^2)*(a^2*y^2 + r^2)^2) 
K_ph,r = ((a^2 - r^2)*a^2*y^2 - a^2*r^2 - 3*r^4)*(y^2 - 1)*a*m/((a^2*y^2 + r^2)^2*sqrt(-(2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) - a^2 - r^2)*(a^2 - 2*m*r + r^2))) 
K_ph,y = -2*sqrt(a^2 - 2*m*r + r^2)*(y^2 - 1)*a^3*m*r*y/(sqrt(-2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) + a^2 + r^2)*(a^2*y^2 + r^2)^2)

<p>The type-(1,1) tensor $K^\sharp$ of components $K^i_{\ \, j} = \gamma^{ik} K_{kj}$:</p>

In [20]:
Ku = K.up(gam, 0)
print(Ku) ; Ku.display()

Tensor field of type (1,1) on the 3-dimensional Riemannian manifold Sigma


(a^5*m*r^2 - 2*a^3*m^2*r^3 + 4*a^3*m*r^4 - 6*a*m^2*r^5 + 3*a*m*r^6 + (a^7*m - 2*a^5*m^2*r + 2*a^3*m^2*r^3 - a^3*m*r^4)*y^4 - (a^7*m - 2*a^5*m^2*r + a^5*m*r^2 + 3*a^3*m*r^4 - 6*a*m^2*r^5 + 3*a*m*r^6)*y^2)*sqrt(a^2*y^2 + r^2)/((a^6*y^6 + 3*a^4*r^2*y^4 + 3*a^2*r^4*y^2 + r^6)*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*sqrt(a^2 - 2*m*r + r^2)) d/dr*dph + 2*(a^3*m*r*y^5 - 2*a^3*m*r*y^3 + a^3*m*r*y)*sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)/((a^6*y^6 + 3*a^4*r^2*y^4 + 3*a^2*r^4*y^2 + r^6)*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)) d/dy*dph + (a^3*m*r^2 + 3*a*m*r^4 - (a^5*m - a^3*m*r^2)*y^2)*sqrt(a^2*y^2 + r^2)/((2*a^2*m*r^3 + a^2*r^4 + r^6 + (a^6 - 2*a^4*m*r + a^4*r^2)*y^4 + 2*(a^4*m*r + a^4*r^2 - a^2*m*r^3 + a^2*r^4)*y^2)*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*sqrt(a^2 - 2*m*r + r^2)) d/dph*dr + 2*sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)*a^3*m*r*y/((2*a^2*m*r^3 + a^2*r^4 + r^6 + (a^6 - 2*a^4*m*r + a^4*r^2)*y^4 + 2*(a^4*m*r + a^4*r^2 - a^2*m*r^3 + a^2*r^4)*y^2)*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)) d/dph*dy

<p>We may check that the hypersurface $\Sigma$ is maximal, i.e. that $K^k_{\ \, k} = 0$:</p>

In [21]:
trK = Ku.trace()
print(trK)
trK.display()

Scalar field zero on the 3-dimensional Riemannian manifold Sigma


zero: Sigma --> R
   (r, y, ph) |--> 0

<h3>Connection and curvature</h3>
<p>Let us call $D$ the Levi-Civita connection associated with $\gamma$: </p>

In [22]:
D = gam.connection(name='D')
print(D) ; D

Levi-Civita connection D associated with the Riemannian metric gam on the 3-dimensional Riemannian manifold Sigma


Levi-Civita connection D associated with the Riemannian metric gam on the 3-dimensional Riemannian manifold Sigma

<p>The Ricci tensor associated with $\gamma$:</p>

In [23]:
Ric = gam.ricci()
print(Ric) ; Ric

Field of symmetric bilinear forms Ric(gam) on the 3-dimensional Riemannian manifold Sigma


Field of symmetric bilinear forms Ric(gam) on the 3-dimensional Riemannian manifold Sigma

In [24]:
Ric.display_comp(only_nonredundant=True)

Ric(gam)_r,r = -(5*a^6*m^2*r^4 + 2*a^4*m^2*r^6 + 8*a^4*m*r^7 - 7*a^2*m^2*r^8 + 7*a^2*m*r^9 + 2*m*r^11 + (a^10*m^2 + 3*a^10*m*r - 14*a^8*m^2*r^2 - 11*a^6*m^2*r^4 + 3*a^6*m*r^5 + 6*(a^8*m + 2*a^6*m^3)*r^3)*y^6 + (3*a^6*m - 4*a^4*m^3)*r^5 - (a^10*m^2 + 9*a^10*m*r - 30*a^8*m^2*r^2 - 35*a^6*m^2*r^4 - 16*a^4*m^2*r^6 + 4*a^4*m*r^7 + (17*a^6*m + 4*a^4*m^3)*r^5 + 2*(11*a^8*m + 12*a^6*m^3)*r^3)*y^4 - (16*a^8*m^2*r^2 + 29*a^6*m^2*r^4 + 18*a^4*m^2*r^6 + 16*a^4*m*r^7 - 7*a^2*m^2*r^8 + 5*a^2*m*r^9 + (17*a^6*m - 8*a^4*m^3)*r^5 + 6*(a^8*m - 2*a^6*m^3)*r^3)*y^2)/(4*a^6*m^2*r^6 + 6*a^4*m*r^9 + 3*a^2*r^12 - 2*m*r^13 + r^14 + (3*a^4 - 8*a^2*m^2)*r^10 + (a^6 - 4*a^4*m^2)*r^8 + (a^14 - 6*a^12*m*r - 6*a^8*m*r^5 + a^8*r^6 + 3*(a^10 + 4*a^8*m^2)*r^4 - 4*(3*a^10*m + 2*a^8*m^3)*r^3 + 3*(a^12 + 4*a^10*m^2)*r^2)*y^8 + 4*(a^6*m - 2*a^4*m^3)*r^7 + 4*(a^12*m*r - 5*a^6*m*r^7 + a^6*r^8 + (3*a^8 + 8*a^6*m^2)*r^6 - (9*a^8*m + 4*a^6*m^3)*r^5 + (3*a^10 + 4*a^8*m^2)*r^4 - (3*a^10*m - 4*a^8*m^3)*r^3 + (a^12 - 4*a^10*m^2)*r^2)*y^6 + 2*(2*a^10*m^2*r^2 + 16*a^6*m^3*r^5 - 12*a^4*m*r^9 + 3*a^4*r^10 + (9*a^6 + 14*a^4*m^2)*r^8 - 2*(9*a^6*m + 2*a^4*m^3)*r^7 + 3*(3*a^8 - 2*a^6*m^2)*r^6 + 3*(a^10 - 6*a^8*m^2)*r^4 + 2*(3*a^10*m - 2*a^8*m^3)*r^3)*y^4 + 4*(2*a^8*m^2*r^4 - 3*a^4*m*r^9 - 3*a^2*m*r^11 + a^2*r^12 + (3*a^4 + 2*a^2*m^2)*r^10 + 3*(a^6 - 2*a^4*m^2)*r^8 + (3*a^6*m + 4*a^4*m^3)*r^7 + (a^8 - 6*a^6*m^2)*r^6 + (3*a^8*m - 4*a^6*m^3)*r^5)*y^2) 
Ric(gam)_r,y = ((3*a^10*m - 4*a^8*m^2*r + 6*a^8*m*r^2 - 8*a^6*m^2*r^3 + 3*a^6*m*r^4)*y^5 + 2*(2*a^8*m^2*r - 3*a^8*m*r^2 + 12*a^6*m^2*r^3 - 6*a^6*m*r^4 + 6*a^4*m^2*r^5 - 3*a^4*m*r^6)*y^3 - (16*a^6*m^2*r^3 + 9*a^6*m*r^4 + 12*a^4*m^2*r^5 + 18*a^4*m*r^6 + 9*a^2*m*r^8)*y)/(4*a^4*m^2*r^6 + 4*a^4*m*r^7 + a^4*r^8 + 4*a^2*m*r^9 + 2*a^2*r^10 + r^12 + (a^12 - 4*a^10*m*r - 4*a^8*m*r^3 + a^8*r^4 + 2*(a^10 + 2*a^8*m^2)*r^2)*y^8 + 4*(a^10*m*r - 2*a^8*m*r^3 - 3*a^6*m*r^5 + a^6*r^6 + 2*(a^8 + a^6*m^2)*r^4 + (a^10 - 2*a^8*m^2)*r^2)*y^6 + 2*(2*a^8*m^2*r^2 + 6*a^8*m*r^3 - 6*a^4*m*r^7 + 3*a^4*r^8 + 2*(3*a^6 + a^4*m^2)*r^6 + (3*a^8 - 8*a^6*m^2)*r^4)*y^4 + 4*(2*a^6*m^2*r^4 + 3*a^6*m*r^5 + 2*a^4*m*r^7 + 2*a^4*r^8 - a^2*m*r^9 + a^2*r^10 + (a^6 - 2*a^4*m^2)*r^6)*y^2) 
Ric(gam)_y,y = (6*a^6*m^2*r^4 + 4*a^4*m^2*r^6 + 7*a^4*m*r^7 - 2*a^2*m^2*r^8 + 5*a^2*m*r^9 + m*r^11 + 2*(3*a^10*m*r - 10*a^8*m^2*r^2 - 10*a^6*m^2*r^4 + 3*a^6*m*r^5 + 2*(3*a^8*m + 4*a^6*m^3)*r^3)*y^6 + (3*a^6*m - 8*a^4*m^3)*r^5 - (9*a^10*m*r - 34*a^8*m^2*r^2 - 36*a^6*m^2*r^4 - 2*a^4*m^2*r^6 - a^4*m*r^7 + (7*a^6*m + 8*a^4*m^3)*r^5 + (17*a^8*m + 32*a^6*m^3)*r^3)*y^4 - 2*(7*a^8*m^2*r^2 + 11*a^6*m^2*r^4 + 3*a^4*m^2*r^6 + 7*a^4*m*r^7 - a^2*m^2*r^8 + 2*a^2*m*r^9 + 8*(a^6*m - a^4*m^3)*r^5 + (3*a^8*m - 8*a^6*m^3)*r^3)*y^2)/(4*a^4*m^2*r^6 + 4*a^4*m*r^7 + a^4*r^8 + 4*a^2*m*r^9 + 2*a^2*r^10 + r^12 - (a^12 - 4*a^10*m*r - 4*a^8*m*r^3 + a^8*r^4 + 2*(a^10 + 2*a^8*m^2)*r^2)*y^10 + (a^12 - 8*a^10*m*r + 4*a^8*m*r^3 + 12*a^6*m*r^5 - 4*a^6*r^6 - (7*a^8 + 8*a^6*m^2)*r^4 - 2*(a^10 - 6*a^8*m^2)*r^2)*y^8 + 2*(2*a^10*m*r - 10*a^8*m*r^3 - 6*a^6*m*r^5 + 6*a^4*m*r^7 - 3*a^4*r^8 - 2*(2*a^6 + a^4*m^2)*r^6 + (a^8 + 12*a^6*m^2)*r^4 + 2*(a^10 - 3*a^8*m^2)*r^2)*y^6 + 2*(2*a^8*m^2*r^2 + 6*a^8*m*r^3 - 6*a^6*m*r^5 - 10*a^4*m*r^7 - a^4*r^8 + 2*a^2*m*r^9 - 2*a^2*r^10 + 2*(2*a^6 + 3*a^4*m^2)*r^6 + 3*(a^8 - 4*a^6*m^2)*r^4)*y^4 + (8*a^6*m^2*r^4 + 12*a^6*m*r^5 + 4*a^4*m*r^7 + 7*a^4*r^8 - 8*a^2*m*r^9 + 2*a^2*r^10 - r^12 + 4*(a^6 - 3*a^4*m^2)*r^6)*y^2) 
Ric(gam)_ph,ph = (a^6*m^2*r^4 + 4*a^4*m^3*r^5 + 10*a^4*m^2*r^6 + a^4*m*r^7 + 13*a^2*m^2*r^8 + 2*a^2*m*r^9 + m*r^11 + (a^10*m^2 + 3*a^10*m*r - 18*a^8*m^2*r^2 - 15*a^6*m^2*r^4 + 3*a^6*m*r^5 + 2*(3*a^8*m + 10*a^6*m^3)*r^3)*y^8 - (2*a^10*m^2 + 3*a^10*m*r - 38*a^8*m^2*r^2 - 22*a^6*m^2*r^4 + 2*a^4*m^2*r^6 - 5*a^4*m*r^7 - (7*a^6*m - 4*a^4*m^3)*r^5 + (a^8*m + 60*a^6*m^3)*r^3)*y^6 + (a^10*m^2 - 22*a^8*m^2*r^2 + 2*a^6*m^2*r^4 + 14*a^4*m^2*r^6 - 3*a^4*m*r^7 + 13*a^2*m^2*r^8 + a^2*m*r^9 - 3*(3*a^6*m - 4*a^4*m^3)*r^5 - 5*(a^8*m - 12*a^6*m^3)*r^3)*y^4 + (2*a^8*m^2*r^2 - 20*a^6*m^3*r^3 - 10*a^6*m^2*r^4 - 22*a^

In [25]:
Ric[1,1].factor()

-(a^10*m*y^6 + 3*a^10*r*y^6 - 14*a^8*m*r^2*y^6 + 6*a^8*r^3*y^6 + 12*a^6*m^2*r^3*y^6 - 11*a^6*m*r^4*y^6 + 3*a^6*r^5*y^6 - a^10*m*y^4 - 9*a^10*r*y^4 + 30*a^8*m*r^2*y^4 - 22*a^8*r^3*y^4 - 24*a^6*m^2*r^3*y^4 + 35*a^6*m*r^4*y^4 - 17*a^6*r^5*y^4 - 4*a^4*m^2*r^5*y^4 + 16*a^4*m*r^6*y^4 - 4*a^4*r^7*y^4 - 16*a^8*m*r^2*y^2 - 6*a^8*r^3*y^2 + 12*a^6*m^2*r^3*y^2 - 29*a^6*m*r^4*y^2 - 17*a^6*r^5*y^2 + 8*a^4*m^2*r^5*y^2 - 18*a^4*m*r^6*y^2 - 16*a^4*r^7*y^2 + 7*a^2*m*r^8*y^2 - 5*a^2*r^9*y^2 + 5*a^6*m*r^4 + 3*a^6*r^5 - 4*a^4*m^2*r^5 + 2*a^4*m*r^6 + 8*a^4*r^7 - 7*a^2*m*r^8 + 7*a^2*r^9 + 2*r^11)*m/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)^2*(a^2*y^2 + r^2)^2*(a^2 - 2*m*r + r^2))

In [26]:
Ric[1,2].factor()

(3*a^8*y^4 - 4*a^6*m*r*y^4 + 6*a^6*r^2*y^4 - 8*a^4*m*r^3*y^4 + 3*a^4*r^4*y^4 + 4*a^6*m*r*y^2 - 6*a^6*r^2*y^2 + 24*a^4*m*r^3*y^2 - 12*a^4*r^4*y^2 + 12*a^2*m*r^5*y^2 - 6*a^2*r^6*y^2 - 16*a^4*m*r^3 - 9*a^4*r^4 - 12*a^2*m*r^5 - 18*a^2*r^6 - 9*r^8)*a^2*m*y/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)^2*(a^2*y^2 + r^2)^2)

In [27]:
Ric[1,3]

0

In [28]:
Ric[2,2].factor()

-(6*a^10*y^6 - 20*a^8*m*r*y^6 + 12*a^8*r^2*y^6 + 16*a^6*m^2*r^2*y^6 - 20*a^6*m*r^3*y^6 + 6*a^6*r^4*y^6 - 9*a^10*y^4 + 34*a^8*m*r*y^4 - 17*a^8*r^2*y^4 - 32*a^6*m^2*r^2*y^4 + 36*a^6*m*r^3*y^4 - 7*a^6*r^4*y^4 - 8*a^4*m^2*r^4*y^4 + 2*a^4*m*r^5*y^4 + a^4*r^6*y^4 - 14*a^8*m*r*y^2 - 6*a^8*r^2*y^2 + 16*a^6*m^2*r^2*y^2 - 22*a^6*m*r^3*y^2 - 16*a^6*r^4*y^2 + 16*a^4*m^2*r^4*y^2 - 6*a^4*m*r^5*y^2 - 14*a^4*r^6*y^2 + 2*a^2*m*r^7*y^2 - 4*a^2*r^8*y^2 + 6*a^6*m*r^3 + 3*a^6*r^4 - 8*a^4*m^2*r^4 + 4*a^4*m*r^5 + 7*a^4*r^6 - 2*a^2*m*r^7 + 5*a^2*r^8 + r^10)*m*r/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)^2*(a^2*y^2 + r^2)^2*(y + 1)*(y - 1))

In [29]:
Ric[2,3]

0

In [30]:
Ric[3,3].factor()

(a^10*m*y^6 + 3*a^10*r*y^6 - 18*a^8*m*r^2*y^6 + 6*a^8*r^3*y^6 + 20*a^6*m^2*r^3*y^6 - 15*a^6*m*r^4*y^6 + 3*a^6*r^5*y^6 - a^10*m*y^4 + 20*a^8*m*r^2*y^4 + 5*a^8*r^3*y^4 - 40*a^6*m^2*r^3*y^4 + 7*a^6*m*r^4*y^4 + 10*a^6*r^5*y^4 - 4*a^4*m^2*r^5*y^4 - 2*a^4*m*r^6*y^4 + 5*a^4*r^7*y^4 - 2*a^8*m*r^2*y^2 + 20*a^6*m^2*r^3*y^2 + 9*a^6*m*r^4*y^2 + a^6*r^5*y^2 + 8*a^4*m^2*r^5*y^2 + 12*a^4*m*r^6*y^2 + 2*a^4*r^7*y^2 + 13*a^2*m*r^8*y^2 + a^2*r^9*y^2 - a^6*m*r^4 - 4*a^4*m^2*r^5 - 10*a^4*m*r^6 - a^4*r^7 - 13*a^2*m*r^8 - 2*a^2*r^9 - r^11)*m*(y + 1)*(y - 1)/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 + r^2)^4)

<p>The scalar curvature $R = \gamma^{ij} R_{ij}$:</p>

In [31]:
R = gam.ricci_scalar(name='R')
print(R)
R.display()

Scalar field R on the 3-dimensional Riemannian manifold Sigma


R: Sigma --> R
   (r, y, ph) |--> 2*(a^6*m^2*r^4 + 6*a^4*m^2*r^6 + 9*a^2*m^2*r^8 - (a^10*m^2 - 6*a^8*m^2*r^2 + 8*a^6*m^3*r^3 - 3*a^6*m^2*r^4)*y^6 + (a^10*m^2 - 8*a^8*m^2*r^2 + 16*a^6*m^3*r^3 - 3*a^6*m^2*r^4 - 6*a^4*m^2*r^6)*y^4 + (2*a^8*m^2*r^2 - 8*a^6*m^3*r^3 - a^6*m^2*r^4 - 9*a^2*m^2*r^8)*y^2)/(4*a^4*m^2*r^8 + 4*a^4*m*r^9 + a^4*r^10 + 4*a^2*m*r^11 + 2*a^2*r^12 + r^14 + (a^14 - 4*a^12*m*r - 4*a^10*m*r^3 + a^10*r^4 + 2*(a^12 + 2*a^10*m^2)*r^2)*y^10 + (4*a^12*m*r - 12*a^10*m*r^3 - 16*a^8*m*r^5 + 5*a^8*r^6 + 2*(5*a^10 + 6*a^8*m^2)*r^4 + (5*a^12 - 8*a^10*m^2)*r^2)*y^8 + 2*(2*a^10*m^2*r^2 + 8*a^10*m*r^3 - 4*a^8*m*r^5 - 12*a^6*m*r^7 + 5*a^6*r^8 + 2*(5*a^8 + 3*a^6*m^2)*r^6 + (5*a^10 - 12*a^8*m^2)*r^4)*y^6 + 2*(6*a^8*m^2*r^4 + 12*a^8*m*r^5 + 4*a^6*m*r^7 - 8*a^4*m*r^9 + 5*a^4*r^10 + 2*(5*a^6 + a^4*m^2)*r^8 + (5*a^8 - 12*a^6*m^2)*r^6)*y^4 + (12*a^6*m^2*r^6 + 16*a^6*m*r^7 + 12*a^4*m*r^9 + 10*a^4*r^10 - 4*a^2*m*r^11 + 5*a^2*r^12 + (5*a^6 - 8*a^4*m^2)*r^8)*y^2)

In [32]:
R.expr().factor()

-2*(a^8*y^4 - 6*a^6*r^2*y^4 + 8*a^4*m*r^3*y^4 - 3*a^4*r^4*y^4 + 2*a^6*r^2*y^2 - 8*a^4*m*r^3*y^2 + 6*a^2*r^6*y^2 + a^4*r^4 + 6*a^2*r^6 + 9*r^8)*a^2*m^2*(y + 1)*(y - 1)/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)^2*(a^2*y^2 + r^2)^3)

<h2>3+1 Einstein equations</h2>
<p>Let us check that the vacuum 3+1 Einstein equations are satisfied.</p>
<p>We start by the contraint equations:</p>
<h3>Hamiltonian constraint</h3>

<p>Let us first evaluate the term $K_{ij} K^{ij}$:</p>

In [33]:
Kuu = Ku.up(gam, 1)
trKK = K['_ij']*Kuu['^ij']
print(trKK) ; trKK.display()

Scalar field on the 3-dimensional Riemannian manifold Sigma


Sigma --> R
(r, y, ph) |--> 2*(a^6*m^2*r^4 + 6*a^4*m^2*r^6 + 9*a^2*m^2*r^8 - (a^10*m^2 - 6*a^8*m^2*r^2 + 8*a^6*m^3*r^3 - 3*a^6*m^2*r^4)*y^6 + (a^10*m^2 - 8*a^8*m^2*r^2 + 16*a^6*m^3*r^3 - 3*a^6*m^2*r^4 - 6*a^4*m^2*r^6)*y^4 + (2*a^8*m^2*r^2 - 8*a^6*m^3*r^3 - a^6*m^2*r^4 - 9*a^2*m^2*r^8)*y^2)/(4*a^4*m^2*r^8 + 4*a^4*m*r^9 + a^4*r^10 + 4*a^2*m*r^11 + 2*a^2*r^12 + r^14 + (a^14 - 4*a^12*m*r - 4*a^10*m*r^3 + a^10*r^4 + 2*(a^12 + 2*a^10*m^2)*r^2)*y^10 + (4*a^12*m*r - 12*a^10*m*r^3 - 16*a^8*m*r^5 + 5*a^8*r^6 + 2*(5*a^10 + 6*a^8*m^2)*r^4 + (5*a^12 - 8*a^10*m^2)*r^2)*y^8 + 2*(2*a^10*m^2*r^2 + 8*a^10*m*r^3 - 4*a^8*m*r^5 - 12*a^6*m*r^7 + 5*a^6*r^8 + 2*(5*a^8 + 3*a^6*m^2)*r^6 + (5*a^10 - 12*a^8*m^2)*r^4)*y^6 + 2*(6*a^8*m^2*r^4 + 12*a^8*m*r^5 + 4*a^6*m*r^7 - 8*a^4*m*r^9 + 5*a^4*r^10 + 2*(5*a^6 + a^4*m^2)*r^8 + (5*a^8 - 12*a^6*m^2)*r^6)*y^4 + (12*a^6*m^2*r^6 + 16*a^6*m*r^7 + 12*a^4*m*r^9 + 10*a^4*r^10 - 4*a^2*m*r^11 + 5*a^2*r^12 + (5*a^6 - 8*a^4*m^2)*r^8)*y^2)

The vacuum Hamiltonian constraint equation is 
$$ R + K^2 -K_{ij} K^{ij} = 0 $$

In [34]:
Ham = R + trK^2 - trKK
print(Ham) ; Ham.display()

Scalar field on the 3-dimensional Riemannian manifold Sigma


Sigma --> R
(r, y, ph) |--> 0

### Momentum constraint

In vaccum, the momentum constraint is
$$ D_j K^j_{\ \, i} - D_i K = 0 $$

In [35]:
mom = D(Ku).trace(0,2) - D(trK)
print(mom)
mom.display()

1-form on the 3-dimensional Riemannian manifold Sigma


0

<h3>Dynamical Einstein equations</h3>
<p>Let us first evaluate the symmetric bilinear form $k_{ij} := K_{ik} K^k_{\ \, j}$:</p>

In [36]:
KK = K['_ik']*Ku['^k_j']
print(KK)

Tensor field of type (0,2) on the 3-dimensional Riemannian manifold Sigma


In [37]:
KK1 = KK.symmetrize()
KK == KK1

True

In [38]:
KK = KK1
print(KK)

Field of symmetric bilinear forms on the 3-dimensional Riemannian manifold Sigma


In [39]:
KK.set_name('(KK)')
KK.display_comp()

(KK)_r,r = (a^6*m^2*r^4 + 6*a^4*m^2*r^6 + 9*a^2*m^2*r^8 - (a^10*m^2 - 2*a^8*m^2*r^2 + a^6*m^2*r^4)*y^6 + (a^10*m^2 + 5*a^6*m^2*r^4 - 6*a^4*m^2*r^6)*y^4 - (2*a^8*m^2*r^2 + 5*a^6*m^2*r^4 + 9*a^2*m^2*r^8)*y^2)/(4*a^6*m^2*r^6 + 6*a^4*m*r^9 + 3*a^2*r^12 - 2*m*r^13 + r^14 + (3*a^4 - 8*a^2*m^2)*r^10 + (a^6 - 4*a^4*m^2)*r^8 + (a^14 - 6*a^12*m*r - 6*a^8*m*r^5 + a^8*r^6 + 3*(a^10 + 4*a^8*m^2)*r^4 - 4*(3*a^10*m + 2*a^8*m^3)*r^3 + 3*(a^12 + 4*a^10*m^2)*r^2)*y^8 + 4*(a^6*m - 2*a^4*m^3)*r^7 + 4*(a^12*m*r - 5*a^6*m*r^7 + a^6*r^8 + (3*a^8 + 8*a^6*m^2)*r^6 - (9*a^8*m + 4*a^6*m^3)*r^5 + (3*a^10 + 4*a^8*m^2)*r^4 - (3*a^10*m - 4*a^8*m^3)*r^3 + (a^12 - 4*a^10*m^2)*r^2)*y^6 + 2*(2*a^10*m^2*r^2 + 16*a^6*m^3*r^5 - 12*a^4*m*r^9 + 3*a^4*r^10 + (9*a^6 + 14*a^4*m^2)*r^8 - 2*(9*a^6*m + 2*a^4*m^3)*r^7 + 3*(3*a^8 - 2*a^6*m^2)*r^6 + 3*(a^10 - 6*a^8*m^2)*r^4 + 2*(3*a^10*m - 2*a^8*m^3)*r^3)*y^4 + 4*(2*a^8*m^2*r^4 - 3*a^4*m*r^9 - 3*a^2*m*r^11 + a^2*r^12 + (3*a^4 + 2*a^2*m^2)*r^10 + 3*(a^6 - 2*a^4*m^2)*r^8 + (3*a^6*m + 4*a^4*m^3)*r^7 + (a^8 - 6*a^6*m^2)*r^6 + (3*a^8*m - 4*a^6*m^3)*r^5)*y^2) 
(KK)_r,y = 2*((a^8*m^2*r - a^6*m^2*r^3)*y^5 - (a^8*m^2*r + 3*a^4*m^2*r^5)*y^3 + (a^6*m^2*r^3 + 3*a^4*m^2*r^5)*y)/(4*a^4*m^2*r^6 + 4*a^4*m*r^7 + a^4*r^8 + 4*a^2*m*r^9 + 2*a^2*r^10 + r^12 + (a^12 - 4*a^10*m*r - 4*a^8*m*r^3 + a^8*r^4 + 2*(a^10 + 2*a^8*m^2)*r^2)*y^8 + 4*(a^10*m*r - 2*a^8*m*r^3 - 3*a^6*m*r^5 + a^6*r^6 + 2*(a^8 + a^6*m^2)*r^4 + (a^10 - 2*a^8*m^2)*r^2)*y^6 + 2*(2*a^8*m^2*r^2 + 6*a^8*m*r^3 - 6*a^4*m*r^7 + 3*a^4*r^8 + 2*(3*a^6 + a^4*m^2)*r^6 + (3*a^8 - 8*a^6*m^2)*r^4)*y^4 + 4*(2*a^6*m^2*r^4 + 3*a^6*m*r^5 + 2*a^4*m*r^7 + 2*a^4*r^8 - a^2*m*r^9 + a^2*r^10 + (a^6 - 2*a^4*m^2)*r^6)*y^2) 
(KK)_y,r = 2*((a^8*m^2*r - a^6*m^2*r^3)*y^5 - (a^8*m^2*r + 3*a^4*m^2*r^5)*y^3 + (a^6*m^2*r^3 + 3*a^4*m^2*r^5)*y)/(4*a^4*m^2*r^6 + 4*a^4*m*r^7 + a^4*r^8 + 4*a^2*m*r^9 + 2*a^2*r^10 + r^12 + (a^12 - 4*a^10*m*r - 4*a^8*m*r^3 + a^8*r^4 + 2*(a^10 + 2*a^8*m^2)*r^2)*y^8 + 4*(a^10*m*r - 2*a^8*m*r^3 - 3*a^6*m*r^5 + a^6*r^6 + 2*(a^8 + a^6*m^2)*r^4 + (a^10 - 2*a^8*m^2)*r^2)*y^6 + 2*(2*a^8*m^2*r^2 + 6*a^8*m*r^3 - 6*a^4*m*r^7 + 3*a^4*r^8 + 2*(3*a^6 + a^4*m^2)*r^6 + (3*a^8 - 8*a^6*m^2)*r^4)*y^4 + 4*(2*a^6*m^2*r^4 + 3*a^6*m*r^5 + 2*a^4*m*r^7 + 2*a^4*r^8 - a^2*m*r^9 + a^2*r^10 + (a^6 - 2*a^4*m^2)*r^6)*y^2) 
(KK)_y,y = -4*((a^8*m^2*r^2 - 2*a^6*m^3*r^3 + a^6*m^2*r^4)*y^4 - (a^8*m^2*r^2 - 2*a^6*m^3*r^3 + a^6*m^2*r^4)*y^2)/(4*a^4*m^2*r^6 + 4*a^4*m*r^7 + a^4*r^8 + 4*a^2*m*r^9 + 2*a^2*r^10 + r^12 + (a^12 - 4*a^10*m*r - 4*a^8*m*r^3 + a^8*r^4 + 2*(a^10 + 2*a^8*m^2)*r^2)*y^8 + 4*(a^10*m*r - 2*a^8*m*r^3 - 3*a^6*m*r^5 + a^6*r^6 + 2*(a^8 + a^6*m^2)*r^4 + (a^10 - 2*a^8*m^2)*r^2)*y^6 + 2*(2*a^8*m^2*r^2 + 6*a^8*m*r^3 - 6*a^4*m*r^7 + 3*a^4*r^8 + 2*(3*a^6 + a^4*m^2)*r^6 + (3*a^8 - 8*a^6*m^2)*r^4)*y^4 + 4*(2*a^6*m^2*r^4 + 3*a^6*m*r^5 + 2*a^4*m*r^7 + 2*a^4*r^8 - a^2*m*r^9 + a^2*r^10 + (a^6 - 2*a^4*m^2)*r^6)*y^2) 
(KK)_ph,ph = (a^6*m^2*r^4 + 6*a^4*m^2*r^6 + 9*a^2*m^2*r^8 + (a^10*m^2 - 6*a^8*m^2*r^2 + 8*a^6*m^3*r^3 - 3*a^6*m^2*r^4)*y^8 - 2*(a^10*m^2 - 7*a^8*m^2*r^2 + 12*a^6*m^3*r^3 - 3*a^6*m^2*r^4 - 3*a^4*m^2*r^6)*y^6 + (a^10*m^2 - 10*a^8*m^2*r^2 + 24*a^6*m^3*r^3 - 2*a^6*m^2*r^4 - 6*a^4*m^2*r^6 + 9*a^2*m^2*r^8)*y^4 + 2*(a^8*m^2*r^2 - 4*a^6*m^3*r^3 - a^6*m^2*r^4 - 3*a^4*m^2*r^6 - 9*a^2*m^2*r^8)*y^2)/(2*a^2*m*r^9 + a^2*r^10 + r^12 + (a^12 - 2*a^10*m*r + a^10*r^2)*y^10 + (2*a^10*m*r + 5*a^10*r^2 - 8*a^8*m*r^3 + 5*a^8*r^4)*y^8 + 2*(4*a^8*m*r^3 + 5*a^8*r^4 - 6*a^6*m*r^5 + 5*a^6*r^6)*y^6 + 2*(6*a^6*m*r^5 + 5*a^6*r^6 - 4*a^4*m*r^7 + 5*a^4*r^8)*y^4 + (8*a^4*m*r^7 + 5*a^4*r^8 - 2*a^2*m*r^9 + 5*a^2*r^10)*y^2)

<p>In vacuum and for stationary spacetimes, the dynamical Einstein equations are
$$ \mathcal{L}_\beta K_{ij} - D_i D_j N + N \left( R_{ij} + K K_{ij} - 2 K_{ik} K^k_{\ \, j}\right) = 0 $$

In [40]:
dyn = K.lie_der(b) - D(D(N)) + N*( Ric + trK*K - 2*KK )
print(dyn)
dyn.display()

Tensor field of type (0,2) on the 3-dimensional Riemannian manifold Sigma


0

## Electric and magnetic parts of the Weyl tensor

The **electric part** is the bilinear form $E$ given by 
$$ E_{ij} = R_{ij} + K K_{ij} - K_{ik} K^k_{\ \, j} $$

In [41]:
E = Ric + trK*K - KK
print(E)

Field of symmetric bilinear forms on the 3-dimensional Riemannian manifold Sigma


In [42]:
E.set_name('E')
E.display_comp(only_nonzero=False)

E_r,r = -(3*a^4*m*r^3 - 2*a^2*m^2*r^4 + 5*a^2*m*r^5 + 2*m*r^7 + 3*(a^6*m*r - 2*a^4*m^2*r^2 + a^4*m*r^3)*y^4 - (9*a^6*m*r - 6*a^4*m^2*r^2 + 16*a^4*m*r^3 - 2*a^2*m^2*r^4 + 7*a^2*m*r^5)*y^2)/(2*a^4*m*r^5 + 2*a^2*r^8 - 2*m*r^9 + r^10 + (a^4 - 4*a^2*m^2)*r^6 + (a^10 - 4*a^8*m*r - 4*a^6*m*r^3 + a^6*r^4 + 2*(a^8 + 2*a^6*m^2)*r^2)*y^6 + (2*a^8*m*r - 8*a^6*m*r^3 - 10*a^4*m*r^5 + 3*a^4*r^6 + 2*(3*a^6 + 4*a^4*m^2)*r^4 + (3*a^8 - 4*a^6*m^2)*r^2)*y^4 + (4*a^6*m*r^3 - 4*a^4*m*r^5 - 8*a^2*m*r^7 + 3*a^2*r^8 + 2*(3*a^4 + 2*a^2*m^2)*r^6 + (3*a^6 - 8*a^4*m^2)*r^4)*y^2) 
E_r,y = 3*((a^6*m + a^4*m*r^2)*y^3 - 3*(a^4*m*r^2 + a^2*m*r^4)*y)/(2*a^2*m*r^5 + a^2*r^6 + r^8 + (a^8 - 2*a^6*m*r + a^6*r^2)*y^6 + (2*a^6*m*r + 3*a^6*r^2 - 4*a^4*m*r^3 + 3*a^4*r^4)*y^4 + (4*a^4*m*r^3 + 3*a^4*r^4 - 2*a^2*m*r^5 + 3*a^2*r^6)*y^2) 
E_r,ph = 0 
E_y,r = 3*((a^6*m + a^4*m*r^2)*y^3 - 3*(a^4*m*r^2 + a^2*m*r^4)*y)/(2*a^2*m*r^5 + a^2*r^6 + r^8 + (a^8 - 2*a^6*m*r + a^6*r^2)*y^6 + (2*a^6*m*r + 3*a^6*r^2 - 4*a^4*m*r^3 + 3*a^4*r^4)*y^4 + (4*a^4*m*r^3 + 3*a^4*r^4 - 2*a^2*m*r^5 + 3*a^2*r^6)*y^2) 
E_y,y = -(3*a^4*m*r^3 - 4*a^2*m^2*r^4 + 4*a^2*m*r^5 + m*r^7 + 6*(a^6*m*r - 2*a^4*m^2*r^2 + a^4*m*r^3)*y^4 - (9*a^6*m*r - 12*a^4*m^2*r^2 + 14*a^4*m*r^3 - 4*a^2*m^2*r^4 + 5*a^2*m*r^5)*y^2)/((a^8 - 2*a^6*m*r + a^6*r^2)*y^8 - 2*a^2*m*r^5 - a^2*r^6 - r^8 - (a^8 - 4*a^6*m*r - 2*a^6*r^2 + 4*a^4*m*r^3 - 3*a^4*r^4)*y^6 - (2*a^6*m*r + 3*a^6*r^2 - 8*a^4*m*r^3 + 2*a^2*m*r^5 - 3*a^2*r^6)*y^4 - (4*a^4*m*r^3 + 3*a^4*r^4 - 4*a^2*m*r^5 + 2*a^2*r^6 - r^8)*y^2) 
E_y,ph = 0 
E_ph,r = 0 
E_ph,y = 0 
E_ph,ph = (2*a^2*m^2*r^4 + a^2*m*r^5 + m*r^7 + 3*(a^6*m*r - 2*a^4*m^2*r^2 + a^4*m*r^3)*y^6 - (3*a^6*m*r - 12*a^4*m^2*r^2 + a^4*m*r^3 - 2*a^2*m^2*r^4 - 2*a^2*m*r^5)*y^4 - (6*a^4*m^2*r^2 + 2*a^4*m*r^3 + 4*a^2*m^2*r^4 + 3*a^2*m*r^5 + m*r^7)*y^2)/(a^8*y^8 + 4*a^6*r^2*y^6 + 6*a^4*r^4*y^4 + 4*a^2*r^6*y^2 + r^8)

Let us factorize the components for a shorter display:

In [43]:
for i in range(1,4):
    for j in range(i,4):
        comp = E[i,j]
        if comp:  # factorization attempted for nonzero components
            comp.factor()
E.display_comp(only_nonzero=False)

E_r,r = -(a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 - 3*a^4 + 2*a^2*m*r - 5*a^2*r^2 - 2*r^4)*(3*a^2*y^2 - r^2)*m*r/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 + r^2)^2*(a^2 - 2*m*r + r^2)) 
E_r,y = 3*(a^2*y^2 - 3*r^2)*(a^2 + r^2)*a^2*m*y/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 + r^2)^2) 
E_r,ph = 0 
E_y,r = 3*(a^2*y^2 - 3*r^2)*(a^2 + r^2)*a^2*m*y/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 + r^2)^2) 
E_y,y = -(2*a^4*y^2 - 4*a^2*m*r*y^2 + 2*a^2*r^2*y^2 - 3*a^4 + 4*a^2*m*r - 4*a^2*r^2 - r^4)*(3*a^2*y^2 - r^2)*m*r/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 + r^2)^2*(y + 1)*(y - 1)) 
E_y,ph = 0 
E_ph,r = 0 
E_ph,y = 0 
E_ph,ph = (a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(3*a^2*y^2 - r^2)*m*r*(y + 1)*(y - 1)/(a^2*y^2 + r^2)^4

The **magnetic part** is the bilinear form $B$ defined by
$$ B_{ij} = \epsilon^k_{\ \, i l} D_k K^l_{\ \, j}, $$
where $\epsilon^k_{\ \, i l}$ are the components of the type-(1,2) tensor $\epsilon^\sharp$, related to the Levi-Civita alternating tensor $\epsilon$ associated with $\gamma$ by $\epsilon^k_{\ \, i l} = \gamma^{km} \epsilon_{m i l}$. In SageManifolds, $\epsilon$ is obtained by the command `volume_form()` and $\epsilon^\sharp$ by the command `volume_form(1)` (`1` = one index raised):

In [44]:
eps = gam.volume_form() 
print(eps) ; eps.display()

3-form eps_gam on the 3-dimensional Riemannian manifold Sigma


eps_gam = sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*sqrt(a^2*y^2 + r^2)/sqrt(a^2 - 2*m*r + r^2) dr/\dy/\dph

In [45]:
epsu = gam.volume_form(1)
print(epsu) ; epsu.display()

Tensor field of type (1,2) on the 3-dimensional Riemannian manifold Sigma


sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*sqrt(a^2 - 2*m*r + r^2)/sqrt(a^2*y^2 + r^2) d/dr*dy*dph - sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*sqrt(a^2 - 2*m*r + r^2)/sqrt(a^2*y^2 + r^2) d/dr*dph*dy + sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*(y^2 - 1)/(sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)) d/dy*dr*dph - sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*(y^2 - 1)/(sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)) d/dy*dph*dr - sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*(a^2*y^2 + r^2)^(3/2)/(((a^4 - 2*a^2*m*r + a^2*r^2)*y^4 - 2*a^2*m*r - a^2*r^2 - r^4 - (a^4 - 4*a^2*m*r - r^4)*y^2)*sqrt(a^2 - 2*m*r + r^2)) d/dph*dr*dy + sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*(a^2*y^2 + r^2)^(3/2)/(((a^4 - 2*a^2*m*r + a^2*r^2)*y^4 - 2*a^2*m*r - a^2*r^2 - r^4 - (a^4 - 4*a^2*m*r - r^4)*y^2)*sqrt(a^2 - 2*m*r + r^2)) d/dph*dy*dr

In [46]:
DKu = D(Ku)
B = epsu['^k_il']*DKu['^l_jk']
print(B)

Tensor field of type (0,2) on the 3-dimensional Riemannian manifold Sigma


<p>Let us check that $B$ is symmetric:</p>

In [47]:
B1 = B.symmetrize()
B == B1

True

<p>Accordingly, we set</p>

In [48]:
B = B1
B.set_name('B')
print(B)

Field of symmetric bilinear forms B on the 3-dimensional Riemannian manifold Sigma


As we did for $E$, we factorize the components of $B$ before displaying them:

In [49]:
for i in range(1,4):
    for j in range(i,4):
        comp = B[i,j]
        if comp:  # factorization attempted for nonzero components
            comp.factor()
B.display_comp(only_nonzero=False)

B_r,r = (a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 - 3*a^4 + 2*a^2*m*r - 5*a^2*r^2 - 2*r^4)*(a^2*y^2 - 3*r^2)*a*m*y/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 + r^2)^2*(a^2 - 2*m*r + r^2)) 
B_r,y = 3*(3*a^2*y^2 - r^2)*(a^2 + r^2)*a*m*r/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 + r^2)^2) 
B_r,ph = 0 
B_y,r = 3*(3*a^2*y^2 - r^2)*(a^2 + r^2)*a*m*r/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 + r^2)^2) 
B_y,y = (2*a^4*y^2 - 4*a^2*m*r*y^2 + 2*a^2*r^2*y^2 - 3*a^4 + 4*a^2*m*r - 4*a^2*r^2 - r^4)*(a^2*y^2 - 3*r^2)*a*m*y/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 + r^2)^2*(y + 1)*(y - 1)) 
B_y,ph = 0 
B_ph,r = 0 
B_ph,y = 0 
B_ph,ph = -(a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 - 3*r^2)*a*m*(y + 1)*(y - 1)*y/(a^2*y^2 + r^2)^4